# Evaluate building completeness

In support of an ongoing project in Nigeria, we are investigating and evaluating the results of a building digitization effort. The following analyses will be performed to assess the completeness of the digitization effort.

1. Attribute evaluation  
   a. ensure variables in verification protocol are present  
   b. ensure relationship between parcel owner and building occupants  
2. Coverage evaluation  
   a. Calculate across the area in a consistently sized grid (250m)  
   b. Compare building density to Google Buildings  

In [1]:
import sys, os, importlib
import folium, fiona

import pandas as pd
import geopandas as gpd
import GOSTRocks.rasterMisc as rMisc
import GOSTRocks.misc as misc

from shapely.geometry import Point, box
from shapely.wkt import loads

from math import ceil
import numpy as np
from shapely.geometry import Polygon

import bldg_helper as helper

%load_ext autoreload
%autoreload 2

In [21]:
in_folder =  "/home/wb411133/projects/NGA_buildings/Abia"
out_folder = os.path.join(in_folder, "Results")
if not os.path.exists(out_folder):
    os.makedirs(out_folder)

#Define inputs
gdb = os.path.join(in_folder, "AbiaStateSFTASPropertyEnumerationDatabase.gdb")
in_da = os.path.join(os.path.dirname(in_folder), "Abia_buildings.shp")
in_aoi = os.path.join(os.path.dirname(in_folder), 'NGA_buildings_aois.shp')
buildings_lyr = 'Digitized_Building_Outlines_Sub'    
# Define paramters
crs = 3857
m_crs = f'epsg:{crs}' # projection used to calculate metre measurements
res = 250 # resolution of 

# Define outputs
summary_grid    = os.path.join(out_folder, f"Abia_summary_grid_{res}.shp")
out_google_csv  = os.path.join(out_folder, "google_buildings.csv")
out_google_bldg = os.path.join(out_folder, "google_buildings.geojson")
da_buildings    = os.path.join(out_folder, "da_buildings.shp")

In [3]:
gdb_layers = fiona.listlayers(gdb)
gdb_layers

['Umuahia_Plotted_Parcels_Sub',
 'Umuahia_Extrapolated_Parcels_Sub',
 'Umuahia_NoParcels_Points_Sub',
 'Ohafia_Plotted_Parcels_Sub',
 'Ohafia_Extrapolated_Parcels_Sub',
 'Ohafia_NoParcels_Points_Sub',
 'Aba_Plotted_Parcels_Sub',
 'Aba_Extrapolated_Parcels_Sub',
 'Aba_NoParcels_Points_Sub',
 'Grids_1000m',
 'StreetCenterLines',
 'LGA_Boundaries',
 'Digitized_Building_Outlines_Sub']

In [9]:
inAOI = gpd.read_file(in_aoi)
inAOI = inAOI.loc[inAOI['Name'].apply(lambda x: "Abia" in x)]
inAOI

id   Name                                           geometry
13  0.0  Abia1  POLYGON ((7.34404 5.25957, 7.35163 5.24028, 7....
14  0.0  Abia2  POLYGON ((7.39698 5.46470, 7.39357 5.53072, 7....
15  0.0  Abia3  POLYGON ((7.62907 5.72333, 7.63043 5.73695, 7....

In [12]:
inB = gpd.read_file(gdb, driver="FileGDB", layer=buildings_lyr)
inB.head()

GridCode   Plot_Size  FloorSpace Created_By Edited_By  \
0  OHA-R50  282.422718  282.422718                        
1  OHA-R50  226.233463  226.233463                        
2  OHA-R50  357.783787  357.783787                        
3  OHA-R50  346.278594  346.278594                        
4  OHA-R50  354.881271  354.881271                        

                  Date_Creat                 Date_Edite  ParcelID Access  \
0  1899-12-30T00:00:00+00:00  1899-12-30T00:00:00+00:00  158151.0     no   
1  1899-12-30T00:00:00+00:00  1899-12-30T00:00:00+00:00  158153.0     no   
2  1899-12-30T00:00:00+00:00  1899-12-30T00:00:00+00:00  158146.0     no   
3  1899-12-30T00:00:00+00:00  1899-12-30T00:00:00+00:00  158170.0     no   
4  1899-12-30T00:00:00+00:00  1899-12-30T00:00:00+00:00  158152.0     no   

           NoAccessType  ... longitude  latitude       alt  \
0  Uncompleted Building  ...  7.718333  5.703465  151.8736   
1  Uncompleted Building  ...  7.720402  5.703372  160.0224   
2            Not Around  ...  7.719213  5.707348  144.8324   
3            Not Around  ...  7.719476  5.705520  181.8020   
4  Uncompleted Building  ...  7.720384  5.706141  178.4610   

                               Picture CustomerID Shape_Length_12  \
0  L:\ATT_Picture2-20210918-130041.jpg    52290.0       67.993316   
1  L:\ATT_Picture2-20210918-115259.jpg    48263.0       61.235848   
2  L:\ATT_Picture2-20210918-105434.jpg    52285.0       84.262601   
3  L:\ATT_Picture2-20210918-124207.jpg    52291.0       77.498295   
4  L:\ATT_Picture2-20210918-123637.jpg    48262.0       78.982405   

  Shape_Area_12 Shape_Length  Shape_Area  \
0    282.422718    67.993316  282.422718   
1    226.233463    61.235848  226.233463   
2    357.783787    84.262601  357.783787   
3    346.278594    77.498295  346.278594   
4    354.881271    78.982405  354.881271   

                                            geometry  
0  MULTIPOLYGON (((358099.205 630509.402, 358100....  
1  MULTIPOLYGON (((358304.854 630514.502, 358321....  
2  MULTIPOLYGON (((358144.016 630942.585, 358170....  
3  MULTIPOLYGON (((358181.748 630721.625, 358185....  
4  MULTIPOLYGON (((358281.907 630792.697, 358295....  

[5 rows x 30 columns]

# Extract buildings from Digitize Africa


In [22]:
importlib.reload(helper)
if not os.path.exists(da_buildings):
    inDA = helper.extract_da_buildings(inAOI, in_da, m_crs)
    inDA.to_file(da_buildings)
else:
    inDA = gpd.read_file(da_buildings)

# Tabulate Parcels
Parcels in Abia are stored in two feaature classes: Plotted Parcels and Extrapolated Parcels, and are spearated by location. These need to be combined to be summarized.

In [35]:
in_parcels = [gpd.read_file(gdb, driver="FileGDB", layer=x) for x in gdb_layers if ("Plotted" in x) or ("Extrapolated" in x)]
inP = pd.concat(in_parcels)

# Summarize statistics

In [ ]:
print(f'Total number of buildings: {inB.shape[0]}')
print(f'Total area of buildings: {inB["Shape_Area"].sum()}')
      
print(f'Total number of parcels: {inP.shape[0]}')
print(f'Total area of parcels: {inP["Shape_Area"].sum()}')

# Assess attribute completeness
1. Size of the parcel (based on polygon)
2. **Number of structures in parcel, number of occupancy units**  
   a. This is not found in the parcel datasets, but can be calculated.
3. The use of each structure and unit
4. The name, ID, and contact details for the owner of the parcel, and the owner or occupier of the structure, or unit


In [37]:
# Calculate null values in parcels dataset
print(f'Total Records: {inP.shape[0]}')
for col in inP.columns:
    cur_col = inP.loc[:,col]
    print(f'{col}: {cur_col.isna().sum()}')

Total Records: 220749
globalid: 113404
Access: 318
NoAccessType: 22504
StageofConstruction: 193779
StickerNo: 33829
PropertyClusterType: 102420
TypeofEnclosure: 102892
NoOfBuildings: 170517
GridNo: 756
LGA: 86
Ward: 216462
District: 1646
EnumerationDate: 86
PlotNo: 219888
HouseNo: 216899
StreetName: 96516
BlockNo: 220345
BuildingStatus: 101939
YearofCompletion: 217511
BuildingType: 102039
Arrangement: 102125
RoofType: 102138
RoofMaterial: 102128
WallMaterial: 102131
Grouping: 106274
FloorNumber: 130158
Water: 102103
Borehole: 102103
Sewerage: 102103
Electricity: 102103
StreetLights: 102103
WasteDisposal: 102103
UnitNo: 220412
UnitType: 101949
UnitPosition: 220537
NoOfRooms: 220634
NoOfUnits: 219790
UnitSize: 220600
GeneralUse: 101811
DetailedUse: 219566
PurposeClause: 170053
Plot_area: 2831
DigitizedBuildingOutline: 124631
longitude: 1036
latitude: 1036
alt: 1036
Remarks: 218682
Team: 97921
LoginofFieldworker: 109935
DateSignedFieldworker: 97627
DeviceID: 113490
CreationDate: 176449
Cr

/tmp/ipykernel_61951/2927440654.py:5: UserWarning: GeoSeries.isna() previously returned True for both missing (None) and empty geometries. Now, it only returns True for missing values. Since the calling GeoSeries contains empty geometries, the result has changed compared to previous versions of GeoPandas.
Given a GeoSeries 's', you can use 's.is_empty | s.isna()' to get back the old behaviour.

To further ignore this warning, you can do: 
import warnings; warnings.filterwarnings('ignore', 'GeoSeries.isna', UserWarning)
  print(f'{col}: {cur_col.isna().sum()}')


In [13]:
# Calculate null values in buildings dataset
print(f'Total Records: {inB.shape[0]}')
for col in inB.columns:
    cur_col = inB.loc[:,col]
    print(f'{col}: {cur_col.isna().sum()}')

Total Records: 321360
GridCode: 1988
Plot_Size: 121834
FloorSpace: 0
Created_By: 1989
Edited_By: 1989
Date_Creat: 1971
Date_Edite: 1989
ParcelID: 120582
Access: 120805
NoAccessType: 137763
StickerNo_1: 138240
LGA: 120582
District: 121910
PlotNo: 319936
HouseNo: 314979
StreetName: 195614
BlockNo: 320674
GeneralUse: 195403
DetailedUse: 318956
PurposeClause: 255083
longitude: 120640
latitude: 120640
alt: 120640
Picture: 163832
CustomerID: 120582
Shape_Length_12: 120582
Shape_Area_12: 120582
Shape_Length: 0
Shape_Area: 0
geometry: 0


# Summarize buildings within a grid

Create a 250m grid across the study arera and summarize bulidngs and parcels within

In [39]:
# Generate the grid
if not os.path.exists(summary_grid):
    grid = helper.generate_grid(inAOI, res, m_crs)
    grid.to_file(summary_grid)
else:
    grid = gpd.read_file(summary_grid)

In [40]:
if inB.crs.to_epsg() != grid.crs.to_epsg():
    inB = inB.to_crs(grid.crs)
    
grid = helper.summarize_in_grid(grid, inDA, inB, inP)

/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError a

/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError a

/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError a

/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError a

/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError a

...

/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError a

/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError a

/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError a

/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError a

/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
  raise InvalidGeometryError("Null geometry supports no operations")
/home/wb411133/.conda/envs/geog/lib/python3.9/site-packages/shapely/topology.py:19: ShapelyDeprecationWarning: InvalidGeometryError will derive from ShapelyError a

In [41]:
grid.to_file(summary_grid)

# RETIRED

In [ ]:
# Summarize buildings in parcels
inP['BLDG_I'] = 0
inP['BLDG_C'] = 0
inP['BLDG_I_G'] = 0
inP['BLDG_C_G'] = 0
for idx, row in inP.iterrows():
    # Summarize collected buildings
    potential_buildings = inB.loc[list(b_idx.intersection(row['geometry'].bounds))]
    m_bld = potential_buildings.loc[~potential_buildings.intersects(row['geometry'])]
    i_bld = potential_buildings.loc[potential_buildings.intersects(row['geometry'])]
    c_bld = potential_buildings.loc[potential_buildings['geometry'].apply(lambda x: row['geometry'].contains(x))]    
    inP.loc[idx, 'BLDG_I'] = i_bld.shape[0]
    inP.loc[idx, 'BLDG_C'] = c_bld.shape[0]
    
    # Summarize buildings in Google
    potential_buildings = inG.loc[list(g_idx.intersection(row['geometry'].bounds))]
    m_bld_g = potential_buildings.loc[~potential_buildings.intersects(row['geometry'])]
    i_bld_g = potential_buildings.loc[potential_buildings.intersects(row['geometry'])]
    c_bld_g = potential_buildings.loc[potential_buildings['geometry'].apply(lambda x: row['geometry'].contains(x))]    
    inP.loc[idx, 'BLDG_I_G'] = i_bld_g.shape[0]
    inP.loc[idx, 'BLDG_C_G'] = c_bld_g.shape[0]
    
    ''' # uncomment this section to stop the loop add a specific index in order to run plotting below
    if idx > 3:
        break
    '''

In [ ]:
m = folium.Map(location=[potential_buildings.unary_union.centroid.y, potential_buildings.unary_union.centroid.x], zoom_start=18)
try:
    folium.GeoJson(row['geometry'], 
             style_function=lambda x: {'fillOpacity':0.5, 'fillColor': 'red', 'color':'#520f0a'}).add_to(m)
except:
    pass
try:
    folium.GeoJson(data=m_bld.to_json(), 
              style_function=lambda x: {'fillOpacity':1,'fillColor': '#ebab15', 'stroke': False}).add_to(m)
except:
    pass
try:
    folium.GeoJson(i_bld.to_json(), 
               style_function=lambda x: {'fillOpacity':1, 'fillColor': '#6878ed', 'stroke': False}).add_to(m)
except:
    pass
try:
    folium.GeoJson(c_bld.to_json(), 
               style_function=lambda x: {'fillOpacity':1, 'fillColor': '#68ed76', 'stroke': False}).add_to(m)
except:
    pass

try:
    folium.GeoJson(data=potential_buildings.to_json(), 
              style_function=lambda x: {'fillOpacity':0,'fillColor': '#ebab15'}).add_to(m)
except:
    pass

m
